In [1]:
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
matplotlib.rcParams['figure.dpi'] = 144
#from requests_futures.sessions import FuturesSession

In [2]:
from static_grader import grader

ModuleNotFoundError: No module named 'static_grader'

In [2]:
import requests
import dill
import pickle
from bs4 import BeautifulSoup
from datetime import datetime
import spacy
from collections import defaultdict
import re

# The New York Social Graph


[New York Social Diary](http://www.newyorksocialdiary.com/) provides a
fascinating lens onto New York's socially well-to-do.  The data forms a natural social graph for New York's social elite.  Take a look at this page of a recent [run-of-the-mill holiday party](http://www.newyorksocialdiary.com/party-pictures/2014/holiday-dinners-and-doers).

Besides the brand-name celebrities, you will notice the photos have carefully annotated captions labeling those that appear in the photos.  We can think of this as implicitly implying a social graph: there is a connection between two individuals if they appear in a picture together.

For this project, we will assemble the social graph from photo captions for parties dated December 1, 2014, and before.  Using this graph, we can make guesses at the most popular socialites, the most influential people, and the most tightly coupled pairs.

We will attack the project in three phases:
1. Get a list of all the photo pages to be analyzed.
2. Parse all of the captions on a sample page.
3. Parse all of the captions on all pages, and assemble the graph.

## Phase One


The first step is to crawl the data.  We want photos from parties on or before December 1st, 2014.  Go to the [Party Pictures Archive](http://www.newyorksocialdiary.com/party-pictures) to see a list of (party) pages.  We want to get the url for each party page, along with its date.

Here are some packages that you may find useful.  You are welcome to use others, if you prefer.

We recommend using Python [Requests](http://docs.python-requests.org/en/master/) to download the HTML pages, and [BeautifulSoup](https://www.crummy.com/software/BeautifulSoup/) to process the HTML.  Let's start by getting the [first page](http://www.newyorksocialdiary.com/party-pictures).

In [4]:
link_url = "http://www.newyorksocialdiary.com"
page = requests.get(link_url+'/party-pictures') # Use requests.get to download the page.

Now, we process the text of the page with BeautifulSoup.

In [5]:
soup = BeautifulSoup(page.text, "lxml")

This page has links to 50 party pages. Look at the structure of the page and determine how to isolate those links.  Your browser's developer tools (usually `Cmd`-`Option`-`I` on Mac, `Ctrl`-`Shift`-`I` on others) offer helpful tools to explore the structure of the HTML page.

Once you have found a pattern, use BeautifulSoup's [select](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#css-selectors) or [find_all](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#find) methods to get those elements.

In [6]:
soup.select('span.views-field.views-field-title a')[0].text

'Full of love'

In [7]:
links = soup.select('div.views-row span a')

There should be 50 per page.

In [8]:
assert len(links) == 50

Let's take a look at that first link.  Figure out how to extract the URL of the link, as well as the date.  You probably want to use `datetime.strptime`.  See the [format codes for dates](https://docs.python.org/2/library/datetime.html#strftime-and-strptime-behavior) for reference.

In [9]:
link = soup.select('div.views-row span a')[0]['href']
# Check that the title and date match what you see visually.
url = link_url+link
dates_lst = soup.select('span.views-field.views-field-created')
date_fmt = datetime.strptime(str(dates_lst[0].text).strip(), '%A, %B %d, %Y')
print(url, date_fmt)

http://www.newyorksocialdiary.com/party-pictures/2018/full-of-love 2018-06-20 00:00:00


For purposes of code reuse, let's put that logic into a function.  It should take the link element and return the URL and date parsed from it.

In [10]:
def get_link_date(el):
    url = link_url+el.select('div.views-row span a')[0]['href']
    dates_lst = el.select('span.views-field.views-field-created')
    date_fmt = datetime.strptime(str(dates_lst[0].text).strip(), '%A, %B %d, %Y')

    return url, date_fmt

In [11]:
get_link_date(soup)

('http://www.newyorksocialdiary.com/party-pictures/2018/full-of-love',
 datetime.datetime(2018, 6, 20, 0, 0))

You may want to check that it works as you expected.

Once that's working, let's write another function to parse all of the links on a page.  Thinking ahead, we can make it take a Requests [Response](http://docs.python-requests.org/en/master/api/#requests.Response) object and do the BeautifulSoup parsing within it.

In [12]:
def get_links(response):
    soup = BeautifulSoup(page.text, "lxml")
    urls = soup.select('div.views-row span a')
    dates = soup.select('span.views-field.views-field-created')
    url_date = []
    for a1, a2 in zip(urls,dates):
        url = link_url + a1['href']
        date_fmt = datetime.strptime(str(a2.text).strip(), '%A, %B %d, %Y')
        url_date.append([url,date_fmt])
    return url_date

If we run this on the previous response, we should get 50 pairs.

In [13]:
assert len(get_links(page)) == 50

But we only want parties with dates on or before the first of December, 2014.  Let's write a function to filter our list of dates to those at or before a cutoff.  Using a keyword argument, we can put in a default cutoff, but allow us to test with others.

In [14]:
def filter_by_date(links, cutoff=datetime(2014, 12, 1)):
    new_list = []
    for url,date in links:
        # Return only the elements with date <= cutoff
        if date <= cutoff:
            new_list.append([url,date])
    return new_list # A list of URL, date pairs        

With the default cutoff, there should be no valid parties on the first page.  Adjust the cutoff date to check that it is actually working.

In [15]:
assert len(filter_by_date(get_links(page))) == 0

Now we should be ready to get all of the party URLs.  Click through a few of the index pages to determine how the URL changes.  Figure out a strategy to visit all of them.

HTTP requests are generally IO-bound.  This means that most of the time is spent waiting for the remote server to respond.  If you use `requests` directly, you can only wait on one response at a time.  [requests-futures](https://github.com/ross/requests-futures) lets you wait for multiple requests at a time.  You may wish to use this to speed up the downloading process.

In [24]:
stop_link = soup.find('li', attrs={'class':'pager__item pager__item--last'})
stop_val = int(stop_link.contents[0]['href'].split('=')[1])

urls = [link_url+'/party-pictures?page=%d'%(i) for i in range(stop_val+1)]

#session = FuturesSession()
#futures = [session.get(url) for url in urls]

link_list = []
for url in urls:
    page = requests.get(url)
    list1 = get_links(page)
#    print(list1)
    list2 = filter_by_date(list1)
    link_list.extend(list2)

In the end, you should have 1193 parties.

In [26]:
assert len(link_list) == 1193

In case we need to restart the notebook, we should save this information to a file.  There are many ways you could do this; here's one using `dill`.

In [27]:
#dill.dump(link_list, open('nysd-links.pkd', 'w'))
pickle.dump( link_list, open( "nysd-links.p", "wb" ), protocol=2)

To restore the list, we can just load it from the file.  When the notebook is restarted, you can skip the code above and just run this command.

In [28]:
link_list = pickle.load(open('nysd-links.p', 'rb'))

## Question 1: histogram


Get the number of party pages for the 95 months (that is, month-year pair) in the data.  Notice that while the party codes might be written as "FRIDAY, FEBRUARY 28, 2014", in this output, you would have to represent the month-year code as "Feb-2014".  This can all be done with `strftime` and the [format codes for dates](https://docs.python.org/2/library/datetime.html#strftime-and-strptime-behavior).

Plot the histogram for yourself.  Do you see any trends?

In [5]:
from collections import defaultdict, OrderedDict, Counter
def histogram():
    dates = []
    for url, date in link_list: dates.append(date)
    sorted_dates = [datetime.strftime(date, "%b-%Y") for date in sorted(dates)]

    ndict = OrderedDict()
    for sdate in sorted_dates:
        if sdate in ndict.keys():
            ndict[sdate] += 1
        else:
            ndict[sdate] = 1 
    fin_list = []
    for key, value in ndict.items():
        fin_list.append((key,value))
    return fin_list  # Replace with the correct list

grader.score(question_name='graph__histogram', func=histogram)

Your score:  1.0


## Phase Two


In this phase, we we concentrate on getting the names out of captions for a given page.  We'll start with [the benefit cocktails and dinner](http://www.newyorksocialdiary.com/party-pictures/2015/celebrating-the-neighborhood) for [Lenox Hill Neighborhood House](http://www.lenoxhill.org/), a neighborhood organization for the East Side.

Take a look at that page.  Note that some of the text on the page is captions, but others are descriptions of the event.  Determine how to select only the captions.

In [7]:
link_list = pickle.load(open('nysd-links.p', 'rb'))

In [52]:
page = requests.get("http://www.newyorksocialdiary.com/party-pictures/2015/celebrating-the-neighborhood")
#page = requests.get(link_list[100][0])
soup = BeautifulSoup(page.text, "lxml")

captions = soup.find_all(attrs={'class': 'photocaption'})

By our count, there are about 110.  But if you're off by a couple, you're probably okay.

In [53]:
assert abs(len(captions) - 110) < 5

Let's encapsulate this in a function.  As with the links pages, we want to avoid downloading a given page the next time we need to run the notebook.  While we could save the files by hand, as we did before, a checkpoint library like [ediblepickle](https://pypi.python.org/pypi/ediblepickle/1.1.3) can handle this for you.  (Note, though, that you may not want to enable this until you are sure that your function is working.)

You should also keep in mind that HTTP requests fail occasionally, for transient reasons.  You should plan how to detect and react to these failures.   The [retrying module](https://pypi.python.org/pypi/retrying) is one way to deal with this.

In [54]:
def get_captions(path):
    page = requests.get("http://www.newyorksocialdiary.com" + path)
    soup = BeautifulSoup(page.text, "lxml")

    return soup.find_all(attrs={'class': 'photocaption'})

This should get the same captions as before.

In [55]:
assert captions == get_captions("/party-pictures/2015/celebrating-the-neighborhood")

Now that we have some sample captions, let's start parsing names out of those captions.  There are many ways of going about this, and we leave the details up to you.  Some issues to consider:

  1. Some captions are not useful: they contain long narrative texts that explain the event.  Try to find some heuristic rules to separate captions that are a list of names from those that are not.  A few heuristics include:
    - look for sentences (which have verbs) and as opposed to lists of nouns. For example, [`nltk` does part of speech tagging](http://www.nltk.org/book/ch05.html) but it is a little slow. There may also be heuristics that accomplish the same thing.
    - Similarly, spaCy's [entity recognition](https://spacy.io/docs/usage/entity-recognition) could be useful here.
    - Look for commonly repeated threads (e.g. you might end up picking up the photo credits or people such as "a friend").
    - Long captions are often not lists of people.  The cutoff is subjective, but for grading purposes, *set that cutoff at 250 characters*.
  2. You will want to separate the captions based on various forms of punctuation.  Try using `re.split`, which is more sophisticated than `string.split`. **Note**: The reference solution uses regex exclusively for name parsing.
  3. You might find a person named "ra Lebenthal".  There is no one by this name.  Can anyone spot what's happening here?
  4. This site is pretty formal and likes to say things like "Mayor Michael Bloomberg" after his election but "Michael Bloomberg" before his election.  Can you find other ('optional') titles that are being used?  They should probably be filtered out because they ultimately refer to the same person: "Michael Bloomberg."
  5. There is a special case you might find where couples are written as eg. "John and Mary Smith". You will need to write some extra logic to make sure this properly parses to two names: "John Smith" and "Mary Smith".
  6. When parsing names from captions, it can help to look at your output frequently and address the problems that you see coming up, iterating until you have a list that looks reasonable. This is the approach used in the reference solution. Because we can only asymptotically approach perfect identification and entity matching, we have to stop somewhere.
  
**Questions worth considering:**
  1. Who is Patrick McMullan and should he be included in the results? How would you address this?
  2. What else could you do to improve the quality of the graph's information?

In [56]:
import spacy
from collections import defaultdict
nlp = spacy.load('en')

textstr = " ".join(map(lambda x: x.text.strip(),captions))

rules_against = ['\xa0','Zombie', 'Hula', 'Thriller']
rules_for = ['Victoire', 'Elijah', 'Kristina', 'Bryna']

names_list = []
names_dict = defaultdict(int)
for caption in captions:
    doc = nlp(caption.text.strip())
    for i, e in enumerate(doc.ents):
        if e.label_ == 'PERSON' or e.text in rules_for:
            name = " ".join(e.text.split())
            if name not in rules_against:
                if len(name.split()) == 1 and i+1 <= len(doc.ents)-1 and name != 'Kathy':
                    name += " " + doc.ents[i+1].text.split()[-1]
                    names_list.append(name)
                    names_dict[name] += 1
                else:
                    names_list.append(name)
                    names_dict[name] += 1
#print(names_list, len(names_list))
#print((set(names_list)))
#print(sorted(names_dict.keys()), len(names_dict.keys()))
pickle.dump( sorted(names_dict.keys()), open( "nysd-names.p", "wb" ), protocol=2 )

## Question 2: sample_names


Once you feel that your algorithm is working well on these captions, parse all of the captions and extract all the names mentioned.  Sort them alphabetically, by first name, and return the first hundred.

In [10]:
def sample_names():
    names_list = pickle.load(open("nysd-names.p", 'rb'))
    return names_list
    
grader.score(question_name='graph__sample_names', func=sample_names)

[u'Glenn Adamson', u'Simon Doonan', u'Craig Leavitt', u'Jerome Chazen', u'Andi Potamkin', u'Ralph Pucci', u'Kirsten Bailey', u'Edwin Hathaway', u'Dennis Freedman', u'Randy Takian', u'Kamie Lightburn', u'Christopher Spitzmiller', u'Christopher Spitzmiller', u'Diana Quasha', u'Mariam Azarm', u'Sana Sabbagh', u'Lynette Dallas', u'Christopher Spitzmiller', u'Sydney Shuman', u'Matthew Bees', u'Christopher Spitzmiller', u'Tom Edelman', u'Warren Scharf', u'Sydney Shuman', u'Sean McAndrew', u'Sydney Shuman', u'Mario Buatta', u'Helene Tilney', u'Katherine DeConti', u'John Rosselli', u'Elizabeth Swartz', u'Stephen Simcock', u'Lee Strock', u'Thomas Hammer', u'Searcy Dryden', u'Lesley Dryden', u'Richard Lightburn', u'Michel Witmer', u'Jennifer Cacioppo', u'Kevin Michael Barba', u'Virginia Wilbanks', u'Valentin Hernandez', u'Yaz Hernandez', u'Chele Farley', u'James Farley', u'Harry Heissmann', u'Angela Clofine', u'Michael Clofine', u'Jared Goss', u'Stewart Ward', u'Alex Papachristidis', u'Mario Bua

Now, run this sort of test on a few other pages.  You will probably find that other pages have a slightly different HTML structure, as well as new captions that trip up your caption parser.  But don't worry if the parser isn't perfect -- just try to get the easy cases.

## Phase Three


Once you are satisfied that your caption scraper and parser are working, run this for all of the pages.  If you haven't implemented some caching of the captions, you probably want to do this first.

In [3]:
link_list = pickle.load(open('nysd-links.p', 'rb'))

In [11]:
def get_captions(path):
    page = requests.get("http://www.newyorksocialdiary.com/" + path)
    soup = BeautifulSoup(page.text, "lxml")
    
    captions = soup.find_all(attrs={'class': 'photocaption'}) #soup.select('div.photocaption')
    cap_list = [capn.text.strip() for capn in captions if capn.text.strip()]
    
    return cap_list

def write_captions(link_list):
    caption_list = []
    score = 0
    score2 = 0
    for link in link_list:
        path = link[0].partition('http://www.newyorksocialdiary.com/')[-1]
        print(path)
        lines = get_captions(path)
        score += len(lines)
        if lines: 
            score2 += len(lines)
            caption_list.extend(lines)
    return caption_list
capn_list = write_captions(link_list)
pickle.dump( capn_list, open( "nysd-captions.p", "wb" ), protocol=2 );

party-pictures/2014/the-thanksgiving-day-parade-from-the-ground-up
party-pictures/2014/gala-guests
party-pictures/2014/equal-justice
party-pictures/2014/celebrating-the-treasures
party-pictures/2014/associates-and-friends
party-pictures/2014/michaels-25th
party-pictures/2014/new-york-lifelines
party-pictures/2014/legends-and-leaders
party-pictures/2014/fall-fun
party-pictures/2014/park-avenue-armorys-2014-gala-masquerade
party-pictures/2014/old-friends-new-friends
party-pictures/2014/new-york-new-york-a-helluva-town
party-pictures/2014/patrons-sponsors-supporters-friends-alumni-and-members
party-pictures/2014/the-fricks-annual-autumn-dinner-and-casita-marias-2014-fiesta
party-pictures/2014/new-york-and-beyond
party-pictures/2014/compassion-choices
party-pictures/2014/public-celebrations
party-pictures/2014/junior-councils-taking-the-lead
party-pictures/2014/luncheons-lectures-and-masked-balls
party-pictures/2014/opening-numbers
party-pictures/2014/the-height-of-style
party-pictures/201

party-pictures/2013/a-changing-world
party-pictures/2013/viva-fiesta
party-pictures/2013/over-the-top-and-under-the-sea
party-pictures/2013/art-awards-and-practical-magic
party-pictures/2013/we-are-their-voice
party-pictures/2013/spring-dinner-dances
party-pictures/2013/spring-galas-and-authors-in-kind
party-pictures/2013/the-elegant-and-the-exclusive
party-pictures/2013/young-fellows-and-masquerades
party-pictures/2013/spring-kickoffs
party-pictures/2013/birthdays-anniversaries-auctions-and-galas
party-pictures/2013/between-the-sheets
party-pictures/2013/celebrating-the-home-front
party-pictures/2013/celebrating-continued-success
party-pictures/2013/the-party-scene
party-pictures/2013/a-winter-ball-and-a-25th-anniversary
party-pictures/2013/intimate-presentations-and-charity-luncheons-and-dinners
party-pictures/2013/pisces-and-partners
party-pictures/2013/party-hopping
party-pictures/2013/exotic-inspirations
party-pictures/2013/gaming-for-a-cause
party-pictures/2013/blizzards-bubbles-

party-pictures/2011/celebrations
party-pictures/2011/fall-feting
party-pictures/2011/bringing-the-crowd-to-their-feet
party-pictures/2011/hulaween-horticulture-and-hostessing
party-pictures/2011/fall-dances-and-dos
party-pictures/2011/taking-action
party-pictures/2011/the-extraordinary-and-exemplary
party-pictures/2011/autumn-dinners
party-pictures/2011/save-a-life
party-pictures/2011/uniforms-and-tuxedos
party-pictures/2011/new-york-after-dark
party-pictures/2011/variations-on-a-theme
party-pictures/2011/galas-appeals-and-childrens-rights
party-pictures/2011/good-times-good-causes
party-pictures/2011/old-fashioned-cocktail-parties-and-galas-dinners
party-pictures/2011/dinner-and-dancing
party-pictures/2011/hope-on-the-horizon
party-pictures/2011/patrons-young-and-old
party-pictures/2011/ballet-balls-and-books
party-pictures/2011/high-marks
party-pictures/2011/fall-galas-come-forth
party-pictures/2011/new-york-needs-you
party-pictures/2011/thanks-for-giving
party-pictures/2011/valentin

party-pictures/2010/dressed-for-the-occasion
party-pictures/2010/end-of-summer-song
party-pictures/2010/keeping-us-on-our-toes-in-the-hamptons
party-pictures/2010/an-unconditional-love-story-and-money-never-sleeps
party-pictures/2010/birthdays-best-buddies-and-book-parties
party-pictures/2010/celebrating-the-soul
party-pictures/2010/strides-for-life
party-pictures/2010/celebrations
party-pictures/2010/more-hamptons-happenings
party-pictures/2010/hamptons-exhibitions-book-parties-and-living-memorials
party-pictures/2010/wild-wild-west-out-east
party-pictures/2010/from-montauk-to-nashville-to-palm-beach
party-pictures/2010/saturday-in-the-hamptons
party-pictures/2010/artcrush-in-aspen
party-pictures/2010/socially-obligatory-for-one-reason-or-another
party-pictures/2010/glorious-summer-afternoons
party-pictures/2010/summer-saturday-afternoons
party-pictures/2010/among-those-attending
party-pictures/2010/summer-gatherings
party-pictures/2010/enchanted-evenings
party-pictures/2010/art-for-l

party-pictures/2009/new-yorkers-for-childrens-10th-annual-fall-gala
party-pictures/2009/abstraction-and-the-real-thing
party-pictures/2009/galas-and-collections
party-pictures/2009/more-from-fashion-week
party-pictures/2009/fashion-week-ongoing
party-pictures/2009/on-with-fashion-week
party-pictures/2009/fashion-week-2009-begins
party-pictures/2009/let-the-fashion-games-begin
party-pictures/2009/elegant-nights-of-sounds-and-style
party-pictures/2009/a-listers
party-pictures/2009/another-hampton-classic
party-pictures/2009/jumping-and-singing
party-pictures/2009/on-our-toes-in-the-hamptons
party-pictures/2009/taking-strides-for-life
party-pictures/2009/best-buddies
party-pictures/2009/moving-summer-along
party-pictures/2009/summer-sun-and-fun
party-pictures/2009/into-the-wee-summer-hours
party-pictures/2009/hamptons-coalitions
party-pictures/2009/the-art-of-fashion-in-the-hamptons
party-pictures/2009/winecrush-in-aspen
party-pictures/2009/hamptons-hoedowns-and-one-to-world
party-picture

party-pictures/2008/waiting-for-reality-rushing-to-completion
party-pictures/2008/the-last-song-of-summer
party-pictures/2008/strides-for-life
party-pictures/2008/welcome-to-the-wonderful-world-of-the-nysd
party-pictures/2008/open-eras
party-pictures/2008/fundraising-galas-and-closing-cermonies
party-pictures/2008/balls-birthdays-and-luncheons
party-pictures/2008/in-the-land-of-rsvp
party-pictures/2008/best-buddies-in-the-hamptons
party-pictures/2008/hampton-summers
party-pictures/2008/art-crushes
party-pictures/2008/summer-and-tropical-thunder
party-pictures/2008/mane-events-in-the-hamptons
party-pictures/2008/midsummer-socials
party-pictures/2008/summer-carnivals
party-pictures/2008/coalitions-and-golden-galas
party-pictures/2008/in-summer-when-the-days-are-long
party-pictures/2008/saving-venice
party-pictures/2008/the-wedding-of-lisa-helene-meiland-and-andrew-james-martin
party-pictures/2008/an-anniversary-of-hope
party-pictures/2008/happy-birthday-leos
party-pictures/2008/uptown-me

party-pictures/2007/cocktails-for-a-cause
party-pictures/2007/guests-of-honor
party-pictures/2007/glitterati-flocks-to-nysd
party-pictures/2007/hamptons-hudson-valley-and-newport
party-pictures/2007/be-ing-kind-in-the-country
party-pictures/2007/uptown-ensembles-and-miami-fashion
party-pictures/2007/southampton-old-and-new
party-pictures/2007/awards-dinners-benefits-and-summer-screenings
party-pictures/2007/from-soho-to-roma
party-pictures/2007/fundraising-and-film
party-pictures/2007/ace-cinema
party-pictures/2007/hollywood-in-the-hamptons
party-pictures/2007/southampton-days-and-nights
party-pictures/2007/houston-arrives-new-yorkers-forever
party-pictures/2007/from-the-hamptons-to-rock-center
party-pictures/2007/friday-fun-and-sun
party-pictures/2007/celebrating-authors-and-the-arts
party-pictures/2007/city-harvest-to-newport-to-new-opera
party-pictures/2007/ajws-cpc-zero-tolerance-nyers-for-children
party-pictures/2007/dance-with-the-dancers
party-pictures/2007/bring-in-the-calvary


In [3]:
captions_html = pickle.load(open( "nysd-captions.p", "rb" ))

In [4]:
len(captions_html)

107527

In [ ]:
#                if not add_last_name:
#                    reline = re.sub(r'|'.join(map(re.escape, tmp_list)), '', line)
#                    nlp = spacy.load('en_core_web_sm')
#                    redoc = nlp(reline)
#                    for i, token in enumerate(redoc):
#                        print(token.text, token.tag_, token.dep_)
#                        name = ""
#                        if e.label_ == 'PERSON':
#                            name = " ".join(e.text.split())
#                            if name not in rules_against and name != "":
#                                if len(name.split()) == 1 and i+1 <= len(doc.ents)-1 \
#                                and name not in names_against and doc.ents[i+1].text.split():
#                                    name += " " + doc.ents[i+1].text.split()[-1]
#                                    tmp_list.append(name)


In [29]:
def sample_names(captions_html):
    rules_against = ['\xa0','Zombie', 'Hula', 'Thriller', 'Patrick McMullan', 'Sprezzatura', 'Jr.', 'Esq',
                    'Epilepsy', 'Seizures','FACES', 'MD', 'Dean', 'NYU', 'Hon' 'Mozart', 'M.D.', 'ABT Dancers'
                    ]
    nlp = spacy.load('en')#
    #nlp = spacy.load('en_core_web_md')

    
    full_list = []
    for jj, line in enumerate(captions_html):
        if not line == "" and not "Photographs by" in line:
            print(jj, "-->", line)
            tmp_list = []
            doc = nlp(line)
            for i, e in enumerate(doc.ents):
                name = ""
                if e.label_ == 'PERSON':# or e.label_ == 'ORG':
                    name = " ".join(e.text.split())
                    if not len(name.split()) > 4 and name != "" and name not in rules_against:
                        if len(name.split()) == 1 and i+1 <= len(doc.ents)-1 and doc.ents[i+1].text.split():
                            name += " " + doc.ents[i+1].text.split()[-1]
                        tmp_list.append(name)
            if tmp_list: full_list.append(sorted(tmp_list))
    return (full_list)

all_caps_list = sample_names(captions_html)
print(len(all_caps_list), all_caps_list)
pickle.dump( all_caps_list, open( "nysd-caption-list.p", "wb" ), protocol=2 );

0 --> The scene at   IDEAL School & Academy’s  10th Annual Gala.
1 --> Les Lieberman, Barri Lieberman, Isabel Kallman, Trish Iervolino, and Ron Iervolino
2 --> Chuck Grodin
3 --> Diana Rosario, Ali Sussman, Sarah Boll, Jen Zaleski, Alysse Brennan, and Lindsay Macbeth
4 --> Kelly  and Tom Murro
5 --> Udo Spreitzenbarth
6 --> Ron Iervolino, Trish Iervolino, Russ Middleton, and Lisa Middleton
7 --> Barbara Loughlin, Dr. Gerald Loughlin, and Debbie Gelston
8 --> Julianne Michelle
9 --> Heather Robinson, Kiwan Nichols, Jimmy Nichols, Melanie Carbone, and Nancy Brown
10 --> Bill Mack and Les Lieberman
11 --> Dr. David Lyden and Patricia Sorenson
12 --> Jimmy Cayne, Vince Tese, and Pat Cayne
13 --> Stuart Oran, Les Lieberman, and Hilary Oran
14 --> Vince Tese and Chuck Grodin
15 --> Dwight Gooden and Les Lieberman
16 --> Dr. Amy Cunningham-Bussel, Ray Mirra, and Dr. Tyler Janovitz
17 --> Dan Shedrick and Samara Heafitz
18 --> Cass and Jason Adelman
19 --> Bart Scott and Mark Laplander
20 --> 

166 --> Lee Mindel, Margaret Russell, Tomas Maier, Martha Stewart, Susan Magrino Dunning
167 --> Bill Katz, Bonnie Morrison, Douglas Friedman, Henry Urbach, Laurie Beckelman, James Sanders, Tony Vidler, and Charles Renfro
168 --> Monica Rich Kosann and Reed Krakoff
169 --> Hendel Teicher
170 --> Henry Urbach and Charles Renfro
171 --> Lori Tritsch and William Lauder
172 --> Margaret Russell in the Sculpture Gallery
173 --> Martha Stewart, Laura Pla, Tomas Maier, and Andrew Preston
174 --> Margaret Russell, Carlos Souza, and Charlene de Ganay
175 --> Hermes Honoree Guillaume de Seuynes, Elizabeth Stribling, and Astrid Stanfield Pinel
176 --> Co-chairs Jean Shafiroff,   CeCe Black, Ursula Lowerre, Ann Van Ness,    Kazie Harvey, and  Deborah Royce
177 --> Guy Robinson, Fernanda Kellogg, and Kirk Henckels
178 --> Bruce Horten and Barbara de Portago
179 --> Dr. Penny Grant and Michel Witmer
180 --> Baroness Laurie Bodor and William Ivey Long
181 --> Cole Rumbough and Bettina Bennett
182 -->

336 --> Michelle Fizer-Peterson, Charles Grodin, and Julio Peterson
337 --> Patrick Murphy and Mary Murphy
338 --> Marco Maccioni
339 --> Jonathan Wald
340 --> Ed Rollins and Shari Rollins
341 --> Per Holmberg and Allyn Magrino Holmberg
342 --> Jamie Niven, Mike Goldberg, Linda Fairstein, and David Patrick Columbia
343 --> Sharon Bush and Oscar Plotkin
344 --> Dick Soloway and Donna Soloway
345 --> Michael McCarty, Sara Beth Shrager, and Rodney Hilton Brown
346 --> George Farias and Wendy Stark
347 --> Claire Mercury and Margo McNabb Nederlander
348 --> Missy Falchi, Carlos Falchi, and Mickey Ateyeh
349 --> Felicia Taylor and Reed Covone
350 --> Paul Chapman and Camila Savia
351 --> Jay Kriegel, Tim Zagat, Nina Zagat, and Gordon Davis
352 --> Katie Lee Pollack and Stephanie Sporn
353 --> Michelle Fizer-Peterson and Julio Peterson
354 --> Diane Clehane, Anne Fulenwider, and Phoebe Eaton
355 --> Paul Amann and Joe Fitzsimmons
356 --> Debra Castel and Stan Parish
357 --> Euan Rellie, Mich

508 --> Katherine Todd and Jaimee Zanzinger
509 --> Michael Pierson, Annette Tapert Allen, and  Lou Howe
510 --> Mark Gilbertson and Kate Allen
511 --> Kamie Lightburn and Scott Anderson
512 --> Olda FitzGerald, Susan Richardson, and Kathrine Richardson
513 --> Spencer Harper, Christina McInerney, Patrick Guinness, and Paula McDermott
514 --> Beth Dater and Michael Kerrigan
515 --> Alexandra Schlesinger, Kenneth Jay Lane, and Olda FitzGerald
516 --> Sean Reynolds, Paula McDermott, Donough Cahill, and Kyra Cheremeteff
517 --> Delia Roche-Kelly, Jose Aguire, and Beatriz Aguire
518 --> Sheila O'Malley Fuchs, Michael Kerrigan, Chantal O'Sullivan, and Kieran McLoughlin
519 --> Jill Donoghue and Robert O'Byrne
520 --> Bob Dowling, Steven Stolman, Michael Kerrigan, and Rich Wilke
521 --> Robert Fox and Anya Fox
522 --> James Anderson, Ivana Lowell, and Steven Gambrel
523 --> Angus Wilke and Cynthia Ryan
524 --> Christopher Monkhouse and William Laffan
525 --> Maribeth Welsh and Tom Quick
526 

648 --> Randy Kemper and Tony Ingrao
649 --> Lonti Ebers
650 --> Wendy Belzberg and Jenny Kassanoff
651 --> Marjorie Reed Gordon and Ellery Gordon
652 --> Elihu Rose, Susan Rose, Isabelle Rose, and Jeffrey Fagen
653 --> Joanne Ellis and Scott Waddell
654 --> Monique Van Vooren and Geoffrey Bradfield
655 --> Michael Feinstein, Cathie Black, Tom Harvey, Adrienne Arsht, and Terrence Flannery
656 --> Juliana May and Amy Silverman
657 --> Serge Tismen, Ida Liu, Michael Rockefeller, and Tara Rockefeller
658 --> Raj Prakash and Stacey Alvarez
659 --> Liz Stern
660 --> Juliana May, Jonathan May, Amy Silverman, and Jeffrey Silverman
661 --> Leslie Bains and Harrison Bains
662 --> Alan Levenstein and Gail Levenstein
663 --> Sara Lese
664 --> Karen Ackman and Bill Ackman
665 --> Tamara Bernstein and Brad Bernstein
666 --> Bonnie Comley, Stewart Lane, and Leah Lane
667 --> Steven Brill and Cynthia Brill
668 --> Jamee Gregory and Peter Gregory
669 --> Michael Shnayerson and Gayfryd Steinberg
670 --

...

106792 --> Hilary Geary Ross and Wilbur Ross
106793 --> Heather Bucha and Frank Whaley
106794 --> Hilary and Bryant Gumbel
106795 --> Celerie Kemble
106796 --> Clo and Charles Cohen
106797 --> Coralie Charriol Paul and Dennis Paul
106798 --> Rachel Zoe
106799 --> Susan Fales Hill
106800 --> Ling Tan
106801 --> Eve
106802 --> Jenny and Malan Breton
106803 --> Simon Hammerstein
106804 --> Lido cabaret
106805 --> The Plastiscines on stage
106806 --> Dalia Obtrlander and Amanda Hearst
106807 --> Jennifer Schofield, Marcello Bottoli, and Beth Thomas Cohen
106808 --> Syl Tang and Susan Redstone
106809 --> Brette Sandler
106810 --> Meredith Dichter, Lorna Montarvo, and Di Petroff
106811 --> Callie Chorne
106812 --> Amy Fine Collins, Richard Lambertson, and Nicole Miller
106813 --> Ali Nichols
106814 --> Beth Ostrosky, Beth Thomas Cohen, and Gillian Hearst
106815 --> Beth Ostrosky and Nicole Miller
106816 --> Beth Thomas Cohen and Callie Chorne
106817 --> Richard Lambertson and Amy Fine Collin

107002 --> Alexis Bryan
107003 --> Elizabeth Saltzman Walker
107004 --> Jim Moore and Madeleine Weeks
107005 --> Ray Kelly and Veronica Kelly
107006 --> Linda Fargo and Dawn Mello
107007 --> Fern Mallis
107008 --> Diana Taylor and Mayor Michael Bloomberg
107009 --> Nadja Swarovski
107010 --> Sylvia Hardin
107011 --> Backstage
107012 --> Elizabeth Joyce, Michele Nadeem, and Ivy Cohen
107013 --> Fabian Basabe and Annie Churchill
107014 --> Fionnan Honan and Chad Thompson
107015 --> Jamee Gregory
107016 --> Gillian Miniter
107017 --> Models with Zac Posen and DHL's Tote for Teachers
107018 --> Sarah Wolfe
107019 --> Olivia Palermo
107020 --> Fern Mallis and Hans Hickler
107021 --> Maggie Betts
107022 --> Zac Posen and his high school English Lit teacher Jane Avrich
107023 --> Kate Schelter
107024 --> Olivia Chantecaille
107025 --> Hamish Bowles
107026 --> Corine Roitfeld and Julia Restoin Roitfeld
107027 --> Alex Lind, Kari Tiederman, and Elizabeth Harrison
107028 --> Andre Leon Talley an

107205 --> Top right: Carole Guess, Mark Epley, Susan Cocke, and Marian Epley. Above, right: Peter Christopoulos.
107206 --> Allie Witt, Barbara Witt, Phil Witt, Mindy Liss, and Howard Brandel
107207 --> Allen, David, and Laura Schlachet
107208 --> Alexa, Kathy, Karina, and Othon Prounis
107209 --> Danielle and David Ganek
107210 --> Emily Post, Kaglean De Monchy, and David Post
107211 --> Ilona, Marina, and Allen Quasha
107212 --> John Catsimatidis and Andrea Catsimatidis
107213 --> Sindy Lutz, Tess DiMenna, Molly Monahan, and Diana DiMenna
107214 --> Cole Uhrig and Vincent Grucci
107215 --> Jack Grimm, Susan Cocke, Phil Cocke, Ann Grimm, and Barbara Smith
107216 --> John Wambold, Melanie Wambold, John Wambold Jr., and George Wambold
107217 --> Kay Gilman and Herb Schmertz
107218 --> The Thomas family
107219 --> Samantha Miller, Sidney Miller, Matt Miller, and Susan Miller
107220 --> Peter Christopoulos, Jean Christopoulos, Dan Christopoulos, and Rebecca Christopoulos
107221 --> Melis

107386 --> Click here for NYSD Contents
107387 --> Click here for NYSD Contents
107388 --> Click here for NYSD Contents
107389 --> Click here for NYSD Contents
107390 --> Click here for NYSD Contents
107391 --> Click here for NYSD Contents
107392 --> Click here for NYSD Contents
107393 --> Click here for NYSD Contents
107394 --> Click here for NYSD Contents
107395 --> Click here for NYSD Contents
107396 --> Click here for NYSD Contents
107397 --> Click here for NYSD Contents
107398 --> Click here for NYSD Contents
107399 --> Click here for NYSD Contents
107400 --> Click here for NYSD Contents
107401 --> Click here for NYSD Contents
107402 --> Click here for NYSD Contents
107403 --> Click here for NYSD Contents
107404 --> Click here for NYSD Contents
107406 --> Click here for NYSD Contents
107407 --> Click here for NYSD Contents
107408 --> Click here for NYSD Contents
107409 --> Click here for NYSD Contents
107410 --> Click here for NYSD Contents
107411 --> Click here for NYSD Contents


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [28]:
pickle.dump( all_caps_list, open( "nysd-caption-list.p", "wb" ), protocol=2 )

In [ ]:
import itertools  # itertools.combinations may be useful
import networkx as nx

All in all, you should end up with over 100,000 captions and more than 110,000 names, connected in about 200,000 pairs.

## Question 3: degree


The simplest question to ask is "who is the most popular"?  The easiest way to answer this question is to look at how many connections everyone has.  Return the top 100 people and their degree.  Remember that if an edge of the graph has weight 2, it counts for 2 in the degree.

**Checkpoint:** Some aggregate stats on the solution

    "count": 100.0
    "mean": 189.92
    "std": 87.8053034454
    "min": 124.0
    "25%": 138.0
    "50%": 157.0
    "75%": 195.0
    "max": 666.0

In [ ]:
import heapq  # Heaps are efficient structures for tracking the largest
              # elements in a collection.  Use introspection to find the
              # function you need.
def degree():
    return [('Alec Baldwin', 144)] * 100

grader.score(question_name='graph__degree', func=degree)

## Question 4: PageRank


A similar way to determine popularity is to look at their
[PageRank](http://en.wikipedia.org/wiki/PageRank).  PageRank is used for web ranking and was originally
[patented](http://patft.uspto.gov/netacgi/nph-Parser?patentnumber=6285999) by Google and is essentially the stationary distribution of a [Markov
chain](http://en.wikipedia.org/wiki/Markov_chain) implied by the social graph.

Use 0.85 as the damping parameter so that there is a 15% chance of jumping to another vertex at random.

**Checkpoint:** Some aggregate stats on the solution

    "count": 100.0
    "mean": 0.0001841088
    "std": 0.0000758068
    "min": 0.0001238355
    "25%": 0.0001415028
    "50%": 0.0001616183
    "75%": 0.0001972663
    "max": 0.0006085816

In [ ]:
def pagerank():
    return [('Martha Stewart', 0.00019312108706213307)] * 100

grader.score(question_name='graph__pagerank', func=pagerank)

## Question 5: best_friends


Another interesting question is who tend to co-occur with each other.  Give us the 100 edges with the highest weights.

Google these people and see what their connection is.  Can we use this to detect instances of infidelity?

**Checkpoint:** Some aggregate stats on the solution

    "count": 100.0
    "mean": 25.84
    "std": 16.0395470855
    "min": 14.0
    "25%": 16.0
    "50%": 19.0
    "75%": 29.25
    "max": 109.0

In [ ]:
def best_friends():
    return [(('Michael Kennedy', 'Eleanora Kennedy'), 41)] * 100

grader.score(question_name='graph__best_friends', func=best_friends)

*Copyright &copy; 2016 The Data Incubator.  All rights reserved.*